# Técnicas de representación de textos
## Introducción a las Ciencias Sociales Computacionales
## Facultad de Ciencias Sociales, Universidad de Buenos Aires, 2023
### Juan Manuel Pérez y Rodolfo Elbert

En esta notebook vamos a realizar análisis muy simples sobre noticias 

In [1]:
from datasets import load_dataset

ds = load_dataset("finiteautomata/prueba-arg", split="train")

ds

Found cached dataset parquet (/users/jmperez/.cache/huggingface/datasets/finiteautomata___parquet/finiteautomata--prueba-arg-1b304d042a671975/0.0.0/2a3b91fbd88a2c90d1dbbb32b460cf621d31bd5b05b934492fdef7d8d6f236ec)


Dataset({
    features: ['tweet_id', 'text', 'title', 'url', 'user', 'body', 'created_at', 'comments'],
    num_rows: 73423
})

In [2]:
# Me quedo con notas con > 20 comentarios

ds = ds.filter(lambda x: len(x['comments']) > 20 and x["title"])

ds

Loading cached processed dataset at /users/jmperez/.cache/huggingface/datasets/finiteautomata___parquet/finiteautomata--prueba-arg-1b304d042a671975/0.0.0/2a3b91fbd88a2c90d1dbbb32b460cf621d31bd5b05b934492fdef7d8d6f236ec/cache-7b100e3bf63f0fee.arrow


Dataset({
    features: ['tweet_id', 'text', 'title', 'url', 'user', 'body', 'created_at', 'comments'],
    num_rows: 35329
})

In [3]:
ds = ds.shuffle().select(range(10_000))

## Embeddings



In [4]:
from sentence_transformers import SentenceTransformer

model_name = "intfloat/multilingual-e5-base"

model = SentenceTransformer(model_name)

In [5]:
titles = ds["title"]
# Hacemos esto por el modelo que usamos
# Ver https://huggingface.co/intfloat/multilingual-e5-base
titles = [f"query: {title}" for title in titles]

embeddings = model.encode(titles, normalize_embeddings=True)



¿Y cómo lo representamos de una manera gráfica? 

Podemos aplicar una reducción de dimensionalidad que "preserve" la distancia entre los puntos, de alguna manera. Por ejemplo, podemos usar la técnica t-SNE (t-distributed Stochastic Neighbor Embedding) que es una técnica de reducción de dimensionalidad no lineal.

In [6]:
# TSNE de sklearn
# PCA de sklearn
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE

# Primero aplico PCA para reducir la dimensionalidad
# Ver https://scikit-learn.org/stable/modules/generated/sklearn.manifold.TSNE.html

pca = PCA(n_components=50)

pca_embeddings = pca.fit_transform(embeddings)
tsne = TSNE(n_components=2, random_state=0)

tsne_embeddings = tsne.fit_transform(pca_embeddings)


In [7]:
# Plotly scatter plot

import plotly.express as px

# Hue el ds["user"]
fig = px.scatter(
    x=tsne_embeddings[:,0], y=tsne_embeddings[:,1], hover_name=titles, color=ds["user"]
)


# Expando el tamaño de la figura

fig.update_layout(
    autosize=False,
    width=1000,
    height=1000,
)

fig.show()


## Identidad de clase



In [8]:
import pandas as pd

df = pd.read_excel("../data/datos_clase.xlsx")

df.to_csv("../data/datos_clase.csv", index=False)

In [9]:
df

id identidad                            justificación identidad
0    1108      Baja                      a veces no llega a fin de mes
1     356      Baja  CLASE ALTA ES CUANDO UNO TIENE ALGO Y YO TODAV...
2     232      Baja  DESDE LO ECONÓMICO, POR EL TIPO DE INGRESO, AD...
3     241      Baja     no gano mucho, lo justo para vivir y hasta ahí
4     620      Baja  no llega con la mínima.con una carrera de 20 a...
..    ...       ...                                                ...
978   172    Obrera  vivir para trabajar no, trabajar para vivir es...
979   337    Obrera                        VIVO TRABAJANDO Y NO AVANZO
980   365    Obrera  Y PORQUE NO TENGO YATE, CASA GRANDE, ME VOY DE...
981   781    Obrera  Y QUE ESTAS OPRIMIDO POR LAS DOS CLASES SOCIAL...
982   986    Obrera                        yo soy un simple trabajador

[983 rows x 3 columns]

In [10]:
textos = df["justificación identidad"].str.lower()

textos = [f"query: {texto.lower()}" for texto in textos]

embeddings = model.encode(textos, normalize_embeddings=True)

In [11]:
# TSNE de sklearn
# PCA de sklearn
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE

# Primero aplico PCA para reducir la dimensionalidad
# Ver https://scikit-learn.org/stable/modules/generated/sklearn.manifold.TSNE.html

pca = PCA(n_components=50)

pca_embeddings = pca.fit_transform(embeddings)
tsne = TSNE(n_components=2)

tsne_embeddings = tsne.fit_transform(pca_embeddings)


In [12]:
# Plotly scatter plot

import plotly.express as px

# Hue el ds["user"]
fig = px.scatter(
    x=tsne_embeddings[:,0], y=tsne_embeddings[:,1], hover_name=textos, color=df["identidad"]
)


# Expando el tamaño de la figura

fig.update_layout(
    autosize=False,
    width=1000,
    height=1000,
)

fig.show()


In [13]:
from umap import UMAP

reducer = UMAP(n_components=2)

umap_embeddings = reducer.fit_transform(embeddings)


In [14]:
# Plotly scatter plot

import plotly.express as px

# Hue el ds["user"]
fig = px.scatter(
    x=umap_embeddings[:,0], y=umap_embeddings[:,1], hover_name=textos, color=df["identidad"]
)


# Expando el tamaño de la figura

fig.update_layout(
    autosize=False,
    width=1000,
    height=1000,
)

fig.show()


In [18]:
# Convertir embeddings a lista de listas

embeddings_lista = [e.tolist() for e in embeddings]

In [19]:
set(type(a) for e in embeddings_lista for a in e)

{float}

In [20]:
# Guardemos todo en chroma

import chromadb

chroma_client = chromadb.Client()
collection = chroma_client.get_or_create_collection(name="descripciones_clase")


In [24]:

collection.add(
    documents=df["justificación identidad"].tolist(),
    embeddings=embeddings_lista,
    metadatas=[{"id": i} for i in df.index],
    ids = [str(i) for i in df.index],
)

In [30]:


def buscar_mas_cercanos(text):
    query = f"query: {text}"
    query_embedding = model.encode(query, normalize_embeddings=True).tolist()

    results = collection.query(query_embedding)

    return results

buscar_mas_cercanos("vivo como un rey")

{'ids': [['553', '975', '185', '66', '149', '10', '633', '964', '539', '131']],
 'distances': [[0.21295717358589172,
   0.21990524232387543,
   0.2262684404850006,
   0.23310615122318268,
   0.23910856246948242,
   0.24133305251598358,
   0.24233786761760712,
   0.24863706529140472,
   0.24863706529140472,
   0.24992115795612335]],
 'metadatas': [[{'id': 553},
   {'id': 975},
   {'id': 185},
   {'id': 66},
   {'id': 149},
   {'id': 10},
   {'id': 633},
   {'id': 964},
   {'id': 539},
   {'id': 131}]],
 'embeddings': None,
 'documents': [['VIVO CON LO JUSTO',
   'vive al día',
   'POR LA FORMA EN QUE VIVE',
   'porque vivo al día',
   'por el ingreso que tengo, por como vivo',
   'POR EL INGRESO QUE UNO TIENE, UNO VIVE COMO PUEDE',
   'por como vive',
   'TRABAJA PARA VIVIR',
   'trabaja para vivir',
   'NO SOY POBRE NI RICO']]}

In [31]:

buscar_mas_cercanos("dependo enteramente de mi trabajo")


{'ids': [['967',
   '641',
   '935',
   '689',
   '843',
   '817',
   '759',
   '757',
   '758',
   '226']],
 'distances': [[0.11931708455085754,
   0.17306581139564514,
   0.17913223803043365,
   0.18032662570476532,
   0.18262511491775513,
   0.18576151132583618,
   0.1885407269001007,
   0.1885407269001007,
   0.1885407269001007,
   0.1894420087337494]],
 'metadatas': [[{'id': 967},
   {'id': 641},
   {'id': 935},
   {'id': 689},
   {'id': 843},
   {'id': 817},
   {'id': 759},
   {'id': 757},
   {'id': 758},
   {'id': 226}]],
 'embeddings': None,
 'documents': [['trabajé siempre y dependo de un sueldo',
   'POR EL TRABAJO QUE TENGO',
   'soy un tipo laburante, un trabajador',
   'porque laburo mucho',
   'porque trabajé toda mi vida',
   'porque toda la vida trabajé',
   'porque siempre trabajé',
   'porque siempre trabajé',
   'porque siempre trabajé',
   'por mi sueldo y por el trabajo que desempeñaba']]}

In [33]:
buscar_mas_cercanos("laburo dia y noche para no morir de hambre")

{'ids': [['747',
   '744',
   '906',
   '904',
   '902',
   '713',
   '40',
   '903',
   '748',
   '745']],
 'distances': [[0.16235414147377014,
   0.1660919338464737,
   0.17642806470394135,
   0.182014599442482,
   0.1833348125219345,
   0.18877369165420532,
   0.19273199141025543,
   0.19312307238578796,
   0.19316044449806213,
   0.19385434687137604]],
 'metadatas': [[{'id': 747},
   {'id': 744},
   {'id': 906},
   {'id': 904},
   {'id': 902},
   {'id': 713},
   {'id': 40},
   {'id': 903},
   {'id': 748},
   {'id': 745}]],
 'embeddings': None,
 'documents': [['porque si no trabajas no comes',
   'PORQUE SI NO TRABAJA NO COME',
   'si no trabaja no come',
   'SI NO SE TRABAJA SE MUERE DE HAMBRE',
   'si el marido no labura no comen',
   'PORQUE NECESITO LABURAR PARA VIVIR',
   'porque no tengo mucho laburo, pero tengo para comer',
   'SI NO SE LABURA NO SE COME',
   'porque si no trabajo no vive mi familia',
   'porque si no trabaja no come, la subsistencia es a diario']]}